In [1]:
import ast
import csv
import json
import reverse_geocoder as rg

import numpy as np
import pandas as pd

import pycountry_convert

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

In [2]:
def country_to_countrycode(country):
    if pd.isna(country):
        return np.nan
    else:
        try:
            return pycountry_convert.country_name_to_country_alpha3(country)
        except:
            return np.nan
        
def countrycode_iso2_to_countrycode_iso3(country):
    if pd.isna(country):
        return np.nan
    else:
        try:
            return pycountry_convert.country_name_to_country_alpha3(pycountry_convert.country_alpha2_to_country_name(country))
        except:
            return np.nan

def countrycode_to_continent(country_code):
    if pd.isna(country_code):
        return np.nan
    else:
        try:
            return pycountry_convert.country_alpha2_to_continent_code(pycountry_convert.country_alpha3_to_country_alpha2(country_code))
        except:
            return np.nan

## Loading datasets

**re3data**

In [3]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t',
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additionalName': ast.literal_eval,
                                    'repositoryIdentifier': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'contentType': ast.literal_eval,
                                    'providerType': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

re3data_df.head()

orgIdentifier                    repositoryName repositoryName.language  \
0  r3d100000001  Odum Institute Archive Dataverse                     eng   
1  r3d100000002      Access to Archival Databases                     eng   
2  r3d100000004    Datenbank Gesprochenes Deutsch                     deu   
3  r3d100000005                     UNC Dataverse                     eng   
4  r3d100000006          Archaeology Data Service                     eng   

                                      additionalName  \
0                                                 []   
1  [{'additionalName': 'AAD', 'additionalNameLang...   
2  [{'additionalName': 'DGD', 'additionalNameLang...   
3  [{'additionalName': 'University of North Carol...   
4  [{'additionalName': 'ADS', 'additionalNameLang...   

                              repositoryURL  \
0  https://dataverse.unc.edu/dataverse/odum   
1             https://aad.archives.gov/aad/   
2              https://dgd.ids-mannheim.de/   
3                https://dataverse.unc.edu/   
4     https://archaeologydataservice.ac.uk/   

                            repositoryIdentifier  \
0                                             []   
1             [RRID:SCR_010479, RRID:nlx_157752]   
2                                             []   
3                                             []   
4  [FAIRsharing_doi:10.25504/FAIRsharing.hm1mfg]   

                                   repositoryContact  \
0  ["https://dataverse.unc.edu/dataverse/odum#", ...   
1               ["https://www.archives.gov/contact"]   
2                            ["dgd@ids-mannheim.de"]   
3  ["https://dataverse.unc.edu/", "odumarchive@un...   
4  ["help@archaeologydataservice.ac.uk", "https:/...   

                                         description description.language  \
0  The Odum Institute Archive Dataverse contains ...                  eng   
1  You will find in the Access to Archival Databa...                  eng   
2  The "Database for Spoken German (DGD)" is a co...                  eng   
3  UNC Dataverse is an open-source repository sof...                  eng   
4  The ADS is an accredited digital repository fo...                  eng   

              type                                               size  \
0   [disciplinary]  {"size": "13 dataverses; 3.050 datasets", "upd...   
1   [disciplinary]                       {"size": "", "updatedp": ""}   
2   [disciplinary]   {"size": "34 corpora", "updatedp": "2020-02-03"}   
3  [institutional]  {"size": "186 dataverses; 25.272 studies; 229....   
4   [disciplinary]  {"size": "1837 results", "updatedp": "2020-05-...   

    startDate endDate repositoryLanguage  \
0         NaN     NaN            ["eng"]   
1        1985     NaN     ["eng", "spa"]   
2        2012     NaN            ["deu"]   
3        2011     NaN            ["eng"]   
4  1996-10-01     NaN            ["eng"]   

                                             subject  \
0  [{'name': '1 Humanities and Social Sciences', ...   
1  [{'name': '1 Humanities and Social Sciences', ...   
2  [{'name': '1 Humanities and Social Sciences', ...   
3  [{'name': '1 Humanities and Social Sciences', ...   
4  [{'name': '1 Humanities and Social Sciences', ...   

                                 missionStatementURL  \
0                                                NaN   
1  https://www.archives.gov/publications/general-...   
2  https://dgd.ids-mannheim.de/dgd/pragdb.dgd_ext...   
3         https://odum.unc.edu/about/mission-vision/   
4  https://archaeologydataservice.ac.uk/about/our...   

                                         contentType  \
0  [{'name': 'Databases', 'scheme': 'parse'}, {'n...   
1  [{'name': 'Images', 'scheme': 'parse'}, {'name...   
2  [{'name': 'Audiovisual data', 'scheme': 'parse...   
3  [{'name': 'Archived data', 'scheme': 'parse'},...   
4  [{'name': 'Archived data', 'scheme': 'parse'},...   

                      providerType  \
0                   [dataProvider]   
1              

In [4]:
re3data_df.describe(include='all')

orgIdentifier repositoryName repositoryName.language additionalName  \
count           2739           2739                    2739           2739   
unique          2739           2736                      19           2162   
top     r3d100000001    Språkbanken                     eng             []   
freq               1              2                    2554            569   

                           repositoryURL repositoryIdentifier  \
count                               2716                 2739   
unique                              2713                  864   
top     http://icgem.gfz-potsdam.de/home                   []   
freq                                   2                 1876   

       repositoryContact                                        description  \
count               2739                                               2739   
unique              2459                                               2737   
top                   []  The National Archives and Records Administrati...   
freq                 202                                                  2   

       description.language            type                          size  \
count                  2739            2739                          2739   
unique                    6               9                          1289   
top                     eng  [disciplinary]  {"size": "", "updatedp": ""}   
freq                   2723            1733                          1450   

       startDate endDate repositoryLanguage  \
count       1776     157               2739   
unique       352      80                107   
top         2008    2015            ["eng"]   
freq          92      11               2063   

                                                  subject  \
count                                                2739   
unique                                               1389   
top     [{'name': '1 Humanities and Social Sciences', ...   
freq                                                  226   

                                      missionStatementURL  \
count                                                2318   
unique                                               2249   
top     https://learn.scholarsportal.info/all-guides/d...   
freq                                                   14   

                                              contentType    providerType  \
count                                                2739            2739   
unique                                               1338               5   
top     [{'name': 'Standard office documents', 'scheme...  [dataProvider]   
freq                                                   30            1771   

                    keyword  \
count                  2739   
unique                 2504   
top     [multidisciplinary]   
freq                    193   

                                              institution policy  \
count                                                2739   2739   
unique                                               2720   2319   
top     [{'institutionName': 'National Center for Biot...   [][]   
freq                                                    6    312   

                                           databaseAccess databaseLicense  \
count                                                2739            2739   
unique                                                 12             375   
top      {"databaseAccessType": "open", "databaseAcces...              []   
freq                                                 2571            2159   

                                               dataAccess  \
count                                                2739   
unique                                                145   
top     [{"dataAccessType": "open", "dataAccessRestric...   
freq                                                 1269   

                                              dataLicense dataUploadType  \
count    

**openDOAR**

In [48]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'repository_metadata.content_subjects': ast.literal_eval,
                                    'repository_metadata.alternativename': ast.literal_eval,
                                    'repository_metadata.content_types': ast.literal_eval,
                                    'organization': ast.literal_eval
                                    },
                         dtype={'system_metadata.id': str})

opendoar_df.head()

system_metadata.id                           repository_metadata.name  \
0                175    {"name": "hku theses online", "language": "en"}   
1                 64  {"name": "research support scheme - central eu...   
2                151  {"name": "cadmus, eui research repository", "l...   
3                105  {"name": "document server@uhasselt", "language...   
4                101  {"name": "utrecht university repository", "lan...   

  repository_metadata.alternativename              repository_metadata.url  \
0                                  []  http://hub.hku.hk/handle/10722/1057   
1                                  []          http://rss.archives.ceu.hu/   
2                                  []                http://cadmus.eui.eu/   
3                                  []   https://doclib.uhasselt.be/dspace/   
4                                  []          http://dspace.library.uu.nl   

                     repository_metadata.description repository_metadata.type  \
0  this is an institutional repository providing ...            institutional   
1  this is an institutional repository collecting...            institutional   
2  cadmus is the name of the eui research reposit...            institutional   
3  this site is a university repository providing...            institutional   
4  this site is a university repository providing...            institutional   

  repository_metadata.content_languages system_metadata.date_modified  \
0                          ["zh", "en"]           2021-03-25 10:16:18   
1              ["cs", "en", "hu", "ru"]           2021-03-25 09:48:31   
2        ["nl", "en", "fr", "de", "it"]           2021-09-13 13:35:36   
3              ["nl", "en", "fr", "de"]           2021-04-16 15:23:52   
4                          ["nl", "en"]           2021-04-16 15:22:03   

  system_metadata.date_created  \
0          2005-12-21 12:44:08   
1          2006-01-04 14:59:30   
2          2006-01-04 12:07:07   
3          2006-01-24 15:46:44   
4          2006-01-13 12:55:13   

                repository_metadata.content_subjects  \
0                                [multidisciplinary]   
1                                [multidisciplinary]   
2  [history and archaeology, multidisciplinary, s...   
3                                [multidisciplinary]   
4                                [multidisciplinary]   

                   repository_metadata.content_types  \
0  [bibliographic_references, theses_and_disserta...   
1                 [unpub_reports_and_working_papers]   
2  [journal_articles, theses_and_dissertations, u...   
3  [journal_articles, conference_and_workshop_pap...   
4  [journal_articles, conference_and_workshop_pap...   

                                        organization  \
0  [{'name': 'university of hong kong', 'alternat...   
1  [{'name': 'central european university', 'alte...   
2  [{'name': 'european university institute', 'al...   
3  [{'name': 'uhasselt', 'alternativeName': 'hass...   
4  [{'name': 'university of utrecht', 'alternativ...   

                                         policy_urls  \
0                                                 []   
1                                                 []   
2  [{"policy_url": "https://www.eui.eu/research/e...   
3                                                 []   
4                                                 []   

                        repository_metadata.software  \
0  {"name": "dspace", "version": "cris-5.3.1-snap...   
1            {"name": "eprints", "version": "2.2.1"}   
2               {"name": "dspace", "version": "5.2"}   
3             {"name": "dspace", "version": "1.7.2"}   
4                  {"name": "dspace", "version": ""}   

                    repository_metadata.oai_url  \
0                                           NaN   
1          http://rss.archives.ceu.hu/perl/oai2   
2              http://cadmus.eui.eu/oai/request   
3  http://doclib.uhasselt.be/dspace-oai/request   
4      http

In [6]:
opendoar_df.describe(include='all')

system_metadata.id                           repository_metadata.name  \
count                5742                                               5742   
unique               5742                                               5713   
top                   175  {"name": "hiroshima associated repository port...   
freq                    1                                                  3   
mean                  NaN                                                NaN   
std                   NaN                                                NaN   
min                   NaN                                                NaN   
25%                   NaN                                                NaN   
50%                   NaN                                                NaN   
75%                   NaN                                                NaN   
max                   NaN                                                NaN   

       repository_metadata.alternativename  \
count                                 5742   
unique                                2108   
top                                     []   
freq                                  3595   
mean                                   NaN   
std                                    NaN   
min                                    NaN   
25%                                    NaN   
50%                                    NaN   
75%                                    NaN   
max                                    NaN   

                   repository_metadata.url  \
count                                 5742   
unique                                5705   
top     http://harp.lib.hiroshima-u.ac.jp/   
freq                                     3   
mean                                   NaN   
std                                    NaN   
min                                    NaN   
25%                                    NaN   
50%                                    NaN   
75%                                    NaN   
max                                    NaN   

                          repository_metadata.description  \
count                                                5421   
unique                                               4619   
top     this site provides access to the research outp...   
freq                                                   95   
mean                                                  NaN   
std                                                   NaN   
min                                                   NaN   
25%                                                   NaN   
50%                                                   NaN   
75%                                                   NaN   
max                                                   NaN   

       repository_metadata.type repository_metadata.content_languages  \
count                      5742                                  5742   
unique                        4                                   330   
top               institutional                                ["en"]   
freq                       5096                                  1917   
mean                        NaN                                   NaN   
std                         NaN                                   NaN   
min                         NaN                                   NaN   
25%                         NaN                                   NaN   
50%                         NaN                                   NaN   
75%                         NaN                                   NaN   
max                         NaN                                   NaN   

       system_metadata.date_modified system_metadata.date_created  \
count                           5742                         5742   
unique                          2372                         5573   
top              2020-09-18 12:53:48          2020-09-18 12:53:48   
freq                              82                  

**ROAR**

In [9]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')
roar_df = roar_df.groupby('eprintid').aggregate(set)

def value_or_list(cell_set):
    copy = set(cell_set)
    copy.discard(np.nan) 
    if len(copy) == 0:
        return np.nan
    if len(copy) == 1:
        return copy.pop()
    return list(copy)
        
roar_df = roar_df.applymap(value_or_list)
roar_df.reset_index(inplace=True)

roar_df.head()

eprintid rev_number eprint_status userid  importid  source  \
0        1        633       archive      1       NaN     NaN   
1       10        511       archive      1       NaN     NaN   
2     1000        274       archive      1       NaN     NaN   
3    10001         20       archive     91       NaN     NaN   
4    10008         11       archive    404       NaN     NaN   

                 dir            datestamp              lastmod  \
0  disk0/00/00/00/01  2010-01-06 13:43:48  2011-07-18 05:40:07   
1  disk0/00/00/00/10  2010-01-06 13:43:48  2011-07-18 05:40:13   
2  disk0/00/00/10/00  2010-01-06 13:45:01  2011-07-06 08:21:21   
3  disk0/00/01/00/01  2015-08-08 14:52:11  2016-03-21 19:44:01   
4  disk0/00/01/00/08  2015-08-08 14:52:26  2016-03-21 19:43:51   

        status_changed           type succeeds  commentary  \
0  2010-01-06 13:43:48        subject      NaN         NaN   
1  2010-01-06 13:43:48  institutional      NaN         NaN   
2  2010-01-06 13:45:01        subject      NaN         NaN   
3  2015-08-08 14:52:11        subject      NaN         NaN   
4  2015-08-08 14:52:26  institutional      NaN         NaN   

  metadata_visibility  latitude  longitude  relation_type  relation_uri  \
0                show       NaN        NaN            NaN           NaN   
1                show       NaN        NaN            NaN           NaN   
2                show       NaN        NaN            NaN           NaN   
3                show       NaN        NaN            NaN           NaN   
4                show       NaN        NaN            NaN           NaN   

  item_issues_id item_issues_type item_issues_description  \
0            NaN              NaN                     NaN   
1            NaN              NaN                     NaN   
2            NaN              NaN                     NaN   
3            NaN              NaN                     NaN   
4            NaN              NaN                     NaN   

  item_issues_timestamp item_issues_status  item_issues_reported_by  \
0                   NaN                NaN                      NaN   
1                   NaN                NaN                      NaN   
2                   NaN                NaN                      NaN   
3                   NaN                NaN                      NaN   
4                   NaN                NaN                      NaN   

   item_issues_resolved_by  item_issues_comment item_issues_count  \
0                      NaN                  NaN                 0   
1                      NaN                  NaN                 0   
2                      NaN                  NaN                 0   
3                      NaN                  NaN               NaN   
4                      NaN                  NaN               NaN   

   sword_depositor  sword_slug exemplar  \
0              NaN         NaN      NaN   
1              NaN         NaN      NaN   
2              NaN         NaN      NaN   
3              NaN         NaN      NaN   
4              NaN         NaN      NaN   

                                     home_page  \
0              http://archivesic.ccsd.cnrs.fr/   
1              http://www.diva-portal.org/mdh/   
2                      http://pam.pisharp.org/   
3  http://edoc.sub.uni-hamburg.de/klimawandel/   
4          http://creativematter.skidmore.edu/   

                                               title  \
0                                        @RCHIVESIC    
1  Academic Archive On-line (Mälardalen Universit...   
2            PAM - Portuguese Archive of Mathematics   
3                       Klimawandel Dokumentenserver   
4        Creative Matter | Skidmore College Research   

                                          oai_pmh sword_endpoint  \
0      http://archivesic.ccsd.cnrs.fr/oai/oai.php            NaN   
1          http://www.diva-portal.org/oai/mdh/OAI            NaN   
2                                             NaN            NaN   
3  http://edoc.sub

In [12]:
roar_df.describe(include='all')

eprintid rev_number eprint_status userid  importid  source  \
count      5375       5375          5375   5375       0.0     0.0   
unique     5375        658             1   2135       NaN     NaN   
top           1         11       archive      1       NaN     NaN   
freq          1        332          5375   1333       NaN     NaN   
mean        NaN        NaN           NaN    NaN       NaN     NaN   
std         NaN        NaN           NaN    NaN       NaN     NaN   
min         NaN        NaN           NaN    NaN       NaN     NaN   
25%         NaN        NaN           NaN    NaN       NaN     NaN   
50%         NaN        NaN           NaN    NaN       NaN     NaN   
75%         NaN        NaN           NaN    NaN       NaN     NaN   
max         NaN        NaN           NaN    NaN       NaN     NaN   

                      dir            datestamp              lastmod  \
count                5375                 5375                 5375   
unique               5375                 4127                 3966   
top     disk0/00/00/00/01  2010-01-06 13:43:48  2011-07-06 08:24:53   
freq                    1                   16                    8   
mean                  NaN                  NaN                  NaN   
std                   NaN                  NaN                  NaN   
min                   NaN                  NaN                  NaN   
25%                   NaN                  NaN                  NaN   
50%                   NaN                  NaN                  NaN   
75%                   NaN                  NaN                  NaN   
max                   NaN                  NaN                  NaN   

             status_changed           type succeeds  commentary  \
count                  5375           5375      107         0.0   
unique                 4158             12      107         NaN   
top     2010-01-06 13:43:48  institutional    10164         NaN   
freq                     16           3795        1         NaN   
mean                    NaN            NaN      NaN         NaN   
std                     NaN            NaN      NaN         NaN   
min                     NaN            NaN      NaN         NaN   
25%                     NaN            NaN      NaN         NaN   
50%                     NaN            NaN      NaN         NaN   
75%                     NaN            NaN      NaN         NaN   
max                     NaN            NaN      NaN         NaN   

       metadata_visibility  latitude  longitude  relation_type  relation_uri  \
count                 5375       0.0        0.0            0.0           0.0   
unique                   2       NaN        NaN            NaN           NaN   
top                   show       NaN        NaN            NaN           NaN   
freq                  5334       NaN        NaN            NaN           NaN   
mean                   NaN       NaN        NaN            NaN           NaN   
std                    NaN       NaN        NaN            NaN           NaN   
min                    NaN       NaN        NaN            NaN           NaN   
25%                    NaN       NaN        NaN            NaN           NaN   
50%                    NaN       NaN        NaN            NaN           NaN   
75%                    NaN       NaN        NaN            NaN           NaN   
max                    NaN       NaN        NaN            NaN           NaN   

           item_issues_id item_issues_type  \
count                  63               63   
unique                 48                5   
top     bad_oai_pmh_url_0  duplicate_title   
freq                   15               33   
mean                  NaN              NaN   
std                   NaN              NaN   
min                   NaN              NaN   
25%                   NaN              NaN   
50%                   NaN              NaN   
75%                   NaN              NaN   
max                   NaN              NaN   

      

**FAIRsharing**

In [57]:
with open('../data/raw/fairsharing_dump_api_09_2021.json') as f:
    lines = f.read().splitlines()
    
fairsharing_df = pd.DataFrame(lines)
fairsharing_df.columns = ['json_element']
fairsharing_df['json_element'].apply(json.loads)
fairsharing_df = pd.json_normalize(fairsharing_df['json_element'].apply(json.loads))

fairsharing_df.head()

id                 type     attributes.created-at  \
0  1723  fairsharing-records  2014-11-04T15:23:40.000Z   
1  3101  fairsharing-records  2020-09-16T08:49:13.000Z   
2  2649  fairsharing-records  2018-08-07T20:23:32.000Z   
3  2657  fairsharing-records  2018-08-13T15:12:11.000Z   
4  2078  fairsharing-records  2014-11-04T15:23:40.000Z   

      attributes.updated-at      attributes.metadata.doi  \
0  2021-09-30T11:39:06.829Z  10.25504/FAIRsharing.8t18te   
1  2021-09-30T11:36:45.452Z                          NaN   
2  2021-09-30T11:39:07.898Z                          NaN   
3  2021-09-30T11:37:28.736Z  10.25504/FAIRsharing.tnByoG   
4  2021-09-30T11:34:43.129Z  10.25504/FAIRsharing.3axym7   

                   attributes.metadata.name attributes.metadata.status  \
0                        Cell Image Library                      ready   
1             WHOI Ship Data-Grabber System                      ready   
2  Electron Microscope Public Image Archive                      ready   
3              ClinicalStudyDataRequest.com                      ready   
4   Germplasm Resources Information Network                      ready   

                        attributes.metadata.contacts  \
0  [{'contact-name': 'David Orloff', 'contact-ema...   
1                                                NaN   
2  [{'contact-name': 'General contact', 'contact-...   
3  [{'contact-email': 'support@clinicalstudydatar...   
4           [{'contact-email': 'dbmu@ars-grin.gov'}]   

                       attributes.metadata.homepage  \
0                   http://www.cellimagelibrary.org   
1  http://4dgeo.whoi.edu/shipdata/SDG_shipdata.html   
2           https://www.ebi.ac.uk/pdbe/emdb/empiar/   
3             https://clinicalstudydatarequest.com/   
4                         https://www.ars-grin.gov/   

   attributes.metadata.identifier  \
0                            1723   
1                            3101   
2                            2649   
3                            2657   
4                            2078   

                     attributes.metadata.description  \
0  This library is a public and easily accessible...   
1  The WHOI Ship DataGrabber system provides the ...   
2  EMPIAR, the Electron Microscopy Public Image A...   
3  ClinicalStudyDataRequest.com (CSDR) is a conso...   
4  GRIN provides National Genetic Resources Progr...   

                   attributes.metadata.support-links  \
0  [{'url': 'http://www.cellimagelibrary.org/page...   
1  [{'url': 'http://4dgeo.whoi.edu/shipdata/SDG_o...   
2  [{'url': 'https://www.ebi.ac.uk/support/EMPIAR...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/Pages/Colle...   

   attributes.metadata.year-creation  \
0                             2010.0   
1                             2004.0   
2                             2015.0   
3                             2014.0   
4                             2010.0   

                  attributes.metadata.data-processes  \
0  [{'name': 'live update', 'type': 'data release...   
1  [{'url': 'http://4dgeo.whoi.edu/sdg-bin/dv_mai...   
2  [{'url': 'https://www.ebi.ac.uk/pdbe/emdb/empi...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/', 'name': ...   

             attributes.legacy-ids attributes.fairsharing-registry  \
0  [biodbcore-000180, bsg-d000180]                        Database   
1  [biodbcore-001609, bsg-d001609]                        Database   
2  [biodbcore-001140, bsg-d001140]                        Database   
3  [biodbcore-001149, bsg-d001149]                        Database   
4  [biodbcore-000546, bsg-d000546]                        Database   

  attributes.record-type                            attributes.subjects  \
0             repository                   [Cell Biology, Life Science]   
1             repository  [Earth Science, Water Research, Oceanography]   
2             repository                      [Bioinformatics

In [58]:
fairsharing_df.describe(include='all')

id                 type     attributes.created-at  \
count   1797                 1797                      1797   
unique  1797                    1                      1162   
top     1723  fairsharing-records  2014-11-04T15:23:40.000Z   
freq       1                 1797                       636   
mean     NaN                  NaN                       NaN   
std      NaN                  NaN                       NaN   
min      NaN                  NaN                       NaN   
25%      NaN                  NaN                       NaN   
50%      NaN                  NaN                       NaN   
75%      NaN                  NaN                       NaN   
max      NaN                  NaN                       NaN   

           attributes.updated-at      attributes.metadata.doi  \
count                       1797                         1354   
unique                      1797                         1354   
top     2021-09-30T11:39:06.829Z  10.25504/FAIRsharing.8t18te   
freq                           1                            1   
mean                         NaN                          NaN   
std                          NaN                          NaN   
min                          NaN                          NaN   
25%                          NaN                          NaN   
50%                          NaN                          NaN   
75%                          NaN                          NaN   
max                          NaN                          NaN   

       attributes.metadata.name attributes.metadata.status  \
count                      1797                       1797   
unique                     1796                          4   
top                     OmicsDB                      ready   
freq                          2                       1540   
mean                        NaN                        NaN   
std                         NaN                        NaN   
min                         NaN                        NaN   
25%                         NaN                        NaN   
50%                         NaN                        NaN   
75%                         NaN                        NaN   
max                         NaN                        NaN   

                             attributes.metadata.contacts  \
count                                                1678   
unique                                               1576   
top     [{'contact-name': 'Sam Hokin', 'contact-email'...   
freq                                                    6   
mean                                                  NaN   
std                                                   NaN   
min                                                   NaN   
25%                                                   NaN   
50%                                                   NaN   
75%                                                   NaN   
max                                                   NaN   

           attributes.metadata.homepage  attributes.metadata.identifier  \
count                              1797                     1797.000000   
unique                             1797                             NaN   
top     http://www.cellimagelibrary.org                             NaN   
freq                                  1                             NaN   
mean                                NaN                     2446.100167   
std                                 NaN                      520.058757   
min                                 NaN                     1547.000000   
25%                                 NaN                     1996.000000   
50%                                 NaN                     2445.000000   
75%                                 NaN                     2897.000000   
max                                 NaN                     3346.000000   

                          attributes.metadata.description  \
count                           

## Subjects analysis

**re3data**

In [38]:
re3data_subjects = re3data_df[['orgIdentifier', 'subject']].explode('subject')
re3data_subjects['subject'] = re3data_subjects['subject'].apply(lambda x: x['name'] if x is not np.nan else np.nan)
re3data_subjects

orgIdentifier                             subject
0     r3d100000001    1 Humanities and Social Sciences
0     r3d100000001                 111 Social Sciences
0     r3d100000001             11104 Political Science
0     r3d100000001                       112 Economics
0     r3d100000001  12 Social and Behavioural Sciences
...            ...                                 ...
2738  r3d100013652                         102 History
2738  r3d100013652                105 Literary Studies
2738  r3d100013652                      108 Philosophy
2738  r3d100013652         10801 History of Philosophy
2738  r3d100013652                       11 Humanities

[16654 rows x 2 columns]

In [42]:
data = re3data_subjects.groupby('subject')[['orgIdentifier']].count().sort_values('subject', ascending=False)
data
plot = [
    go.Bar(
        x=data[data.index.str.contains('^\d{%s}\s' % tier, regex=True)].index,
        y=data[data.index.str.contains('^\d{%s}\s' % tier, regex=True)]['orgIdentifier'],
        name='re3data tier %s-digits' % tier
    ) for tier in [1,2,3,5]
] 

layout = go.Layout(
    title='Subject coverage re3data',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)

fig = go.Figure(plot, layout).show()

**OpenDOAR**

In [49]:
opendoar_subjects = opendoar_df.explode('repository_metadata.content_subjects')

In [50]:
data = opendoar_subjects.groupby('repository_metadata.content_subjects')[['system_metadata.id']].count().sort_values('system_metadata.id', ascending=False)
plot = [
    go.Bar(
        x=data.index,
        y=data['system_metadata.id'],
    ) 
] 

layout = go.Layout(
    title='Subject coverage OpenDOAR',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)

fig = go.Figure(plot, layout).show()

**ROAR**

In [55]:
roar_subjects = roar_df.explode('subjects')

In [56]:
data = roar_subjects.groupby('subjects')[['eprintid']].count().sort_values('eprintid', ascending=False)
plot = [
    go.Bar(
        x=data.index,
        y=data['eprintid'],
    ) 
] 

layout = go.Layout(
    title='Subject coverage OpenDOAR',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)

fig = go.Figure(plot, layout).show()

**FAIRsharing**

In [59]:
fairsharing_subjects = fairsharing_df.explode('attributes.subjects')

In [61]:
data = fairsharing_subjects.groupby('attributes.subjects')[['id']].count().sort_values('id', ascending=False)
plot = [
    go.Bar(
        x=data.index,
        y=data['id'],
        name='FAIRsharing'
    )
]

layout = go.Layout(
    title='Subject coverage FAIRsharing',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)

fig = go.Figure(plot, layout).show()

## Geographic analysis

**re3data**

In [21]:
re3data_institutions = re3data_df.explode('institution')[['re3data_id', 'institution']]
re3data_institutions = re3data_institutions[~re3data_institutions.institution.isna()].reset_index(drop=True)
re3data_institutions = re3data_institutions.join(pd.DataFrame(re3data_institutions.institution.to_list(), columns=['org_name', 'org_other_names', 
                                                                                              'org_country', 'org_3', 'org_noprofit', 
                                                                                              'org_url', 'org_ids', 'org_date1', 
                                                                                              'org_date2', 'org_contact']))
re3data_institutions.head()

re3data_id                                        institution  \
0  r3d100000001  [Odum Institute for Research in Social Science...   
1  r3d100000002  [The U.S. National Archives and Records Admini...   
2  r3d100000002  [The USA.gov, [], USA, [general], non-profit, ...   
3  r3d100000004  [Institut für Deutsche Sprache, Archiv für Ges...   
4  r3d100000005  [Odum Institute for Research in Social Science...   

                                            org_name  \
0      Odum Institute for Research in Social Science   
1  The U.S. National Archives and Records Adminis...   
2                                        The USA.gov   
3  Institut für Deutsche Sprache, Archiv für Gesp...   
4      Odum Institute for Research in Social Science   

             org_other_names org_country               org_3 org_noprofit  \
0                         []         USA           [general]   non-profit   
1  [NARA, National Archives]         USA           [general]   non-profit   
2                         []         USA           [general]   non-profit   
3                      [AGD]         DEU  [funding, general]   non-profit   
4                         []         USA         [technical]   non-profit   

                                  org_url org_ids org_date1 org_date2  \
0           https://odum.unc.edu/archive/      []                       
1                http://www.archives.gov/      []                       
2                     http://www.usa.gov/      []                       
3  http://agd.ids-mannheim.de/index.shtml      []      2004             
4                   https://odum.unc.edu/      []                       

                                         org_contact  
0                                                 []  
1                 [http://www.archives.gov/contact/]  
2                 [http://www.usa.gov/Contact.shtml]  
3                              [agd@ids-mannheim.de]  
4  [https://odum.unc.edu/contact/contact-form/, o...

In [22]:
re3data_institutions['org_continent'] = re3data_institutions.org_country.map(countrycode_to_continent)

In [23]:
re3data_institutions[re3data_institutions.org_continent.isna()].org_country.unique()

array(['AAA', 'EEC'], dtype=object)

AAA is used for international collaborations; we skip this.
EEC is used for the EU commission; we fix the continent manually.

In [24]:
re3data_institutions.loc[re3data_institutions.org_country == 'EEC', 'org_continent'] = 'EU'

**OpenDOAR**

In [25]:
opendoar_institutions = opendoar_df.explode('institution')[['opendoar_id', 'institution']]
opendoar_institutions = opendoar_institutions[~opendoar_institutions.institution.isna()].reset_index(drop=True)
opendoar_institutions = opendoar_institutions.join(pd.DataFrame(opendoar_institutions.institution.to_list(), columns=['org_name', 'org_other_names', 
                                                                                              'org_country', 'org_3', 'org_noprofit', 
                                                                                              'org_url', 'org_ids', 'org_date1', 
                                                                                              'org_date2', 'org_contact']))
opendoar_institutions['org_country'] = opendoar_institutions.org_country.map(str.upper, na_action='ignore')
opendoar_institutions['org_country'] = opendoar_institutions.org_country.map(countrycode_iso2_to_countrycode_iso3, na_action='ignore')
opendoar_institutions.head()

opendoar_id                                        institution  \
0          101  [university of utrecht, [universiteit utrecht]...   
1          115  [indian institute of management kozhikode, [ii...   
2           41  [california institute of technology, [caltech]...   
3          119  [dublin city university, [dcu], ie, [], , http...   
4          129  [istituto nazionale di geofisica e vulcanologi...   

                                         org_name         org_other_names  \
0                           university of utrecht  [universiteit utrecht]   
1        indian institute of management kozhikode                  [iimk]   
2              california institute of technology               [caltech]   
3                          dublin city university                   [dcu]   
4  istituto nazionale di geofisica e vulcanologia                  [ingv]   

  org_country org_3 org_noprofit                  org_url  \
0         NLD    []                     https://www.uu.nl   
1         IND    []                http://www.iimk.ac.in/   
2         USA    []               http://www.caltech.edu/   
3         IRL    []                    http://www.dcu.ie/   
4         ITA    []                    http://www.ingv.it   

                       org_ids org_date1 org_date2 org_contact  
0  [https://ror.org/04pp8hn57]                              []  
1  [https://ror.org/03m1xdc36]                              []  
2  [https://ror.org/05dxps055]                              []  
3  [https://ror.org/04a1a1e81]                              []  
4  [https://ror.org/00qps9a02]                              []

In [26]:
opendoar_institutions['org_continent'] = opendoar_institutions.org_country.map(countrycode_to_continent)

In [27]:
opendoar_institutions[opendoar_institutions.org_continent.isna()].org_country.unique()

array([nan, 'UMI'], dtype=object)

In [28]:
opendoar_institutions.loc[opendoar_institutions.org_country == 'UMI', 'org_continent'] = 'NA'
opendoar_institutions[opendoar_institutions.org_country == 'UMI']

opendoar_id                                        institution  \
4349         5379  [kettering university, [], um, [], , https://w...   

                  org_name org_other_names org_country org_3 org_noprofit  \
4349  kettering university              []         UMI    []                

                        org_url                      org_ids org_date1  \
4349  https://www.kettering.edu  [https://ror.org/03rcspa57]             

     org_date2 org_contact org_continent  
4349                    []            NA

**ROAR**

In [29]:
roar_df['location_country'] = roar_df.location_country.map(str.upper, na_action='ignore')
roar_df['location_country'] = roar_df.location_country.map(countrycode_iso2_to_countrycode_iso3)
roar_df['continent'] = roar_df.location_country.map(countrycode_to_continent)

**FAIRsharing**

In [30]:
fairsharing_df['subjects'] = fairsharing_df.subjects.str.split(pat=',')
fairsharing_df['countries'] = fairsharing_df.countries.str.split(pat=',')

fairsharing_countries = fairsharing_df.explode('countries')
fairsharing_countries['countrycode'] = fairsharing_countries.countries.map(country_to_countrycode)
fairsharing_countries['continent'] = fairsharing_countries.countrycode.map(countrycode_to_continent)

In [31]:
fairsharing_countries[fairsharing_countries.countrycode.isna()].countries.unique()

array(['European Union', 'Republic of Ireland', 'Worldwide', nan],
      dtype=object)

In [32]:
fairsharing_countries[fairsharing_countries.continent.isna()].countries.unique()

array(['European Union', 'Republic of Ireland', 'Worldwide', 'Antarctica',
       nan], dtype=object)

Fix manually some rows

In [33]:
fairsharing_countries.loc[fairsharing_countries.countries == 'Republic of Ireland', ['countries', 'countrycode', 'continent']] = ['Ireland', 'IE', 'EU']
fairsharing_countries.loc[fairsharing_countries.countries == 'European Union', ['countrycode', 'continent']] = ['EU', 'EU']

Make Antactica disappear (only one repo)

In [34]:
fairsharing_countries.loc[fairsharing_countries.countries == 'Antarctica', ['countrycode', 'continent']] = ['AQ', np.nan]
fairsharing_countries[fairsharing_countries.countrycode == 'AQ']

full_name  \
915  Antabif IPT - AntOBIS IPT - GBIF Belgium   

                                   short_name  \
915  Antabif IPT - AntOBIS IPT - GBIF Belgium   

                                                fs_url  \
915  https://fairsharing.org/10.25504/FAIRsharing.e...   

                             url   countries                      subjects  \
915  http://ipt.biodiversity.aq/  Antarctica  [Biodiversity, Life Science]   

    countrycode continent  
915          AQ       NaN

### Country coverage

In [35]:
data1 = re3data_institutions.groupby('org_country')[['re3data_id']].count().sort_values('re3data_id', ascending=False)
data2 = opendoar_institutions.groupby('org_country')[['opendoar_id']].count().sort_values('opendoar_id', ascending=False)
data3 = roar_df.groupby('location_country')[['eprintid']].count().sort_values('eprintid', ascending=False)
data4 = fairsharing_countries.groupby('countrycode')[['url']].count().sort_values('url', ascending=False)

plot = [
    go.Bar(
        x=data1.index,
        y=data1['re3data_id'],
        name='re3data'
    ),
    go.Bar(
        x=data2.index,
        y=data2['opendoar_id'],
        name='openDOAR',
        visible = 'legendonly'
    ),
    go.Bar(
        x=data3.index,
        y=data3['eprintid'],
        name='ROAR',
        visible = 'legendonly'
    ),
    go.Bar(
        x=data4.index,
        y=data4['url'],
        name='FAIRsharing',
        visible = 'legendonly'
    )
]

layout = go.Layout(
    title='Country coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)

go.Figure(plot, layout).show()

### Continental coverage

In [36]:
data1 = re3data_institutions.groupby('org_continent')[['re3data_id']].count()
data2 = opendoar_institutions.groupby('org_continent')[['opendoar_id']].count()
data3 = roar_df.groupby('continent')[['eprintid']].count()
data4 = fairsharing_countries.groupby('continent')[['url']].count()

plot = [
    go.Scatterpolar(
        r=data1.re3data_id,
        theta=data1.index,
        fill='toself',
        name='re3data'),
    go.Scatterpolar(
        r=data2.opendoar_id,
        theta=data2.index,
        fill='toself',
        name='OpenDOAR'),
    go.Scatterpolar(
        r=data3.eprintid,
        theta=data3.index,
        fill='toself',
        name='ROAR'),
    go.Scatterpolar(
        r=data4.url,
        theta=data4.index,
        fill='toself',
        name='FAIRsharing')
]

layout = go.Layout(polar=dict(
    radialaxis=dict(
      visible=True
    ),
  )
)

go.Figure(plot, layout).show()